In [ ]:
import PyPDF2, os
import pandas as pd

In [ ]:
def read_pdf(path):
    pdf_file = open(path, 'rb')
    pdf_reader = PyPDF2.PdfReader(pdf_file)
    text = ''
    for page_num in range(len(pdf_reader.pages)):
        page = pdf_reader.pages[page_num]
        text += page.extract_text()
    pdf_file.close()
    return text

invoices = []
path = 'invoices/'

for file in os.listdir(path):
    if file.startswith('invoice'):
        text = read_pdf(path + file)
        print(text)
        invoices.append(text)

In [ ]:
import os
def save_as_csv(details, save_as = "invoice.csv"):
    # if the csv already exists then concat a new one to it, else create a new one
    if os.path.exists(save_as):
        df = pd.read_csv(save_as)
        df = pd.concat([df, pd.DataFrame(details, index=[0])], ignore_index=True)
    else:  
        df = pd.DataFrame(details, index=[0])
    df.to_csv(save_as, index=False)

In [ ]:
import re

def extract_invoice_details(text):
    invoice_details = {}
    try:
        invoice_details['Order Number'] = re.search(r'Order Number: (\S+)', text).group(1)
        invoice_details['Invoice Number'] = re.search(r'Invoice Number : (\S+)', text).group(1)
        invoice_details['Order Date'] = re.search(r'Order Date: (\d{2}\.\d{2}\.\d{4})', text).group(1)
        invoice_details['Invoice Details'] = re.search(r'Invoice Details : (\S+)', text).group(1)
        invoice_details['Invoice Date'] = re.search(r'Invoice Date : (\d{2}\.\d{2}\.\d{4})', text).group(1)
        invoice_details['Billing Address'] = re.search(r'Billing Address :([\s\S]+?)Shipping Address :', text).group(1).strip()
        invoice_details['Shipping Address'] = re.search(r'Shipping Address :([\s\S]+?)Place of supply:', text).group(1).strip()
        invoice_details['PAN'] = re.search(r'PAN No:(\S+)', text).group(1)
    except:
        print('Order Number not found')
    
    item_match = re.search(r'1([\s\S]+?)TOTAL:', text, re.DOTALL)
    if item_match:
        item_info = item_match.group(1)
        item_name = re.search(r'\nAmount\n1([\s\S]+?)₹', item_info).group(1).strip()
        invoice_details['Item'] = item_name
        print(item_name)
    else:
        print("No item found in the invoice.")
    total_mount_match = re.search(r'TOTAL:([\s\S]+?)only', text, re.DOTALL)
    if total_mount_match:
        total_mount = total_mount_match.group(1).split('₹')[2].split('\n')[0]
        invoice_details['Total Amount'] = total_mount
    else:
        print("No total amount found in the invoice.")
    gstin_match = re.search(r'GST Registration No: ([\s\S]+?) ', text)
    if gstin_match:
        invoice_details['GSTIN'] = gstin_match.group(1).strip()
    else:
        print("No GSTIN found in the invoice.")
    by_match = re.search(r'By :([\s\S]+?)PAN No:', text)
    if by_match:
        invoice_details['Sold By'] = by_match.group(1).strip()
    else:
        print("No seller found in the invoice.")
        
    return invoice_details

In [ ]:
for invoice in invoices:
    # print(invoice)
    details = extract_invoice_details(invoice)
    save_as_csv(details)

In [ ]:
df = pd.read_csv('invoice.csv')
df.head(10)

In [8]:
import PyPDF2, os, re
import pandas as pd

class InvoiceConvertor:
    """
    This class is hardcoded to read all pdf files that start with 'invoice' in the given user given path and convert them to a csv file.
    
    Usage:
    convertor = InvoiceConvertor()
    convertor.read_pdfs('path_to_pdfs')
    result_df = convertor.convert()

    """
    def __init__(self):
        self.invoices = []
        
    def read_pdfs(self,path):
        for file in os.listdir(path):
            if file.startswith('invoice'):
                pdf_file = open(path + file, 'rb')
                pdf_reader = PyPDF2.PdfReader(pdf_file)
                text = ''
                for page_num in range(len(pdf_reader.pages)):
                    page = pdf_reader.pages[page_num]
                    text += page.extract_text()
                pdf_file.close()
                self.invoices.append(text)
        return self.invoices
    
    def save_as_csv(self, details, save_as = "invoice.csv"):
        # if the csv already exists then concat a new one to it, else create a new one
        if os.path.exists(save_as):
            df = pd.read_csv(save_as)
            df = pd.concat([df, pd.DataFrame(details, index=[0])], ignore_index=True)
        else:  
            df = pd.DataFrame(details, index=[0])
        df.to_csv(save_as, index=False)
        
    def extract_invoice_details(self, text):
        invoice_details = {}
        try:
            invoice_details['Order Number'] = re.search(r'Order Number: (\S+)', text).group(1)
            invoice_details['Invoice Number'] = re.search(r'Invoice Number : (\S+)', text).group(1)
            invoice_details['Order Date'] = re.search(r'Order Date: (\d{2}\.\d{2}\.\d{4})', text).group(1)
            invoice_details['Invoice Details'] = re.search(r'Invoice Details : (\S+)', text).group(1)
            invoice_details['Invoice Date'] = re.search(r'Invoice Date : (\d{2}\.\d{2}\.\d{4})', text).group(1)
            invoice_details['Billing Address'] = re.search(r'Billing Address :([\s\S]+?)Shipping Address :', text).group(1).strip()
            invoice_details['Shipping Address'] = re.search(r'Shipping Address :([\s\S]+?)Place of supply:', text).group(1).strip()
            invoice_details['PAN'] = re.search(r'PAN No:(\S+)', text).group(1)
        except:
            print('Order Number not found')

        item_match = re.search(r'1([\s\S]+?)TOTAL:', text, re.DOTALL)
        if item_match:
            item_info = item_match.group(1)
            item_name = re.search(r'\nAmount\n1([\s\S]+?)₹', item_info).group(1).strip()
            invoice_details['Item'] = item_name
            # print(item_name)
        else:
            print("No item found in the invoice.")
        total_mount_match = re.search(r'TOTAL:([\s\S]+?)only', text, re.DOTALL)
        if total_mount_match:
            total_mount = total_mount_match.group(1).split('₹')[2].split('\n')[0]
            invoice_details['Total Amount'] = total_mount
        else:
            print("No total amount found in the invoice.")
        gstin_match = re.search(r'GST Registration No: ([\s\S]+?) ', text)
        if gstin_match:
            invoice_details['GSTIN'] = gstin_match.group(1).strip()
        else:
            print("No GSTIN found in the invoice.")
        by_match = re.search(r'By :([\s\S]+?)PAN No:', text)
        if by_match:
            invoice_details['Sold By'] = by_match.group(1).strip()
        else:
            print("No seller found in the invoice.")
        return invoice_details
    
    def convert(self):
        for invoice in self.invoices:
            details = self.extract_invoice_details(invoice)
            self.save_as_csv(details)
        return pd.read_csv('invoice.csv')

In [9]:
invoice_convertor = InvoiceConvertor()
invoice_convertor.read_pdfs('invoices/')
res = invoice_convertor.convert()
res.head(10)

Order Number not found


Order Number Invoice Number  Order Date          Invoice Details  \
0  402-7035529-3886722    NAG1-192347  17.08.2023        MH-NAG1-1034-2324   
1  402-7035529-3886722   BOM5-1379800  17.08.2023        MH-BOM5-1034-2324   
2  405-4419941-9848328      DEX3-4683  23.07.2023   DL-DEX3-157533501-2324   
3  405-4419941-9848328     HYD8-29019  23.07.2023   TG-HYD8-817549015-2324   
4  405-0015964-5687515        IN-5040  23.07.2023       DL-1922955505-2324   
5  408-4974466-7793143    JPX2-223775  02.01.2024  RJ-JPX2-1317922175-2324   
6                  NaN            NaN         NaN                      NaN   

  Invoice Date                                    Billing Address  \
0   17.08.2023  Pratik Dwivedi \nBennett University, Plot Nos ...   
1   17.08.2023  Pratik Dwivedi \nBennett University, Plot Nos ...   
2   23.07.2023  Pratik Dwivedi \nC- 123 Sector 26, Sector 26 N...   
3   23.07.2023  Pratik Dwivedi \nC- 123 Sector 26, Sector 26 N...   
4   23.07.2023  Pratik Dwivedi \nC- 123 Sector 26, Sector 26 N...   
5   02.01.2024  Devpal \n514/3, Ganesh vihar \nROORKEE, UTTARA...   
6          NaN                                                NaN   

                                    Shipping Address         PAN  \
0  Pratik Dwivedi \nPratik Dwivedi \nBennett Univ...  AALCA0171E   
1  Pratik Dwivedi \nPratik Dwivedi \nBennett Univ...  AALCA0171E   
2  Pratik Dwivedi \nPratik Dwivedi \nC- 123 Secto...  ABEPW6057C   
3  Pratik Dwivedi \nPratik Dwivedi \nC- 123 Secto...  AACCN8253B   
4  Pratik Dwivedi \nPratik Dwivedi \nC- 123 Secto...  JISPS4412R   
5  Devpal \nDevpal \n514/3, Ganesh vihar \nROORKE...  AADCV4254H   
6                                                NaN         NaN   

                                                Item Total Amount  \
0  Cosmic Byte CB-EP-05 Wired Gaming in Ear Earph...        458.0   
1  LG Ultragear IPS Gaming Monitor 60 cm (24\nInc...    13,099.00   
2  Amozo Easy Fit Tempered Glass Screen Protector...       474.00   
3  ESR for iPhone 13/14 Cover, Shockproof Drop Pr...       399.00   
4  imluckies Camera Lens Protector Compatible wit...       149.00   
5  Amazon Basics Sleek Rechargeable LED Table Lam...       569.00   
6  Saregama Carvaan Telugu - Portable Music Playe...     6,320.00   

                    GSTIN                                            Sold By  
0         27AALCA0171E1ZZ  Appario Retail Private Ltd \n*TCI Supply Chain...  
1         27AALCA0171E1ZZ  Appario Retail Private Ltd \n*Renaissance indu...  
2         07ABEPW6057C1ZK  RADHIKA WALIA \n*Plot no 28, Block A, Mohan Co...  
3         36AACCN8253B1ZN  TIGER PUG COMMERCE PRIVATE LIMITED \n*GMR Airp...  
4         07JISPS4412R1Z4  M.A.ENTERPRISES \n*D2/235 GALI NO 6, 3rd PUSTA...  
5         08AADCV4254H1Z8  ETRADE MARKETING PRIVATE LIMITED \n*Kh No 554 ...  
6  36AARCA3925C1ZQBilling  AATS Connect Private Limited \n* GMR Airport C...